```
This notebook sets up and runs a test case for analyzing Kelvin waves
Copyright (C) 2018, 2019  SINTEF Digital
Copyright (C) 2018, 2019 Norwegian Meteorological Institute

This notebook implements the Kelvin waves test case, as reported 
under Case D in "Evaluation of Selected Finite-Difference and 
Finite-Volume Approaches to Rotational Shallow-Water Flow" 
by Holm, Brodtkorb, Broström, Christensen and Sætra.

This program is free software: you can redistribute it and/or modify
it under the terms of the GNU General Public License as published by
the Free Software Foundation, either version 3 of the License, or
(at your option) any later version.

This program is distributed in the hope that it will be useful,
but WITHOUT ANY WARRANTY; without even the implied warranty of
MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
GNU General Public License for more details.

You should have received a copy of the GNU General Public License
along with this program.  If not, see <http://www.gnu.org/licenses/>.
```

# Oslofjord
Testing of Nils projected files

In [1]:
#Lets have matplotlib "inline"
%matplotlib inline

import os
import sys

#Import packages we need
import numpy as np
from netCDF4 import Dataset
import datetime
from IPython.display import display

#For plotting
import matplotlib
from matplotlib import pyplot as plt

plt.rcParams["lines.color"] = "w"
plt.rcParams["text.color"] = "w"
plt.rcParams["axes.labelcolor"] = "w"
plt.rcParams["xtick.color"] = "w"
plt.rcParams["ytick.color"] = "w"

plt.rcParams["image.origin"] = "lower"

In [2]:
from gpuocean.utils import IPythonMagic, NetCDFInitialization

In [3]:
%cuda_context_handler gpu_ctx

Path to the test file

In [4]:
source_url = "/sintef/data/OsloFjord/test.nc"

## Inspecting file structure and content

In [5]:
import xarray as xr
ds = xr.open_dataset("/sintef/data/OsloFjord/test.nc")
ds

<xarray.Dataset>
Dimensions:     (ocean_time: 67, s_rho: 42, eta_rho: 746, xi_rho: 388, xi_u: 387, eta_v: 745)
Coordinates:
  * ocean_time  (ocean_time) datetime64[ns] 2022-10-25 ... 2022-10-27T18:00:00
  * s_rho       (s_rho) float64 -0.9881 -0.9643 -0.9405 ... -0.03571 -0.0119
Dimensions without coordinates: eta_rho, xi_rho, xi_u, eta_v
Data variables:
    projection  int32 ...
    Cs_r        (s_rho) float64 ...
    h           (eta_rho, xi_rho) float32 ...
    mask_rho    (eta_rho, xi_rho) float32 ...
    angle       (eta_rho, xi_rho) float32 ...
    zeta        (ocean_time, eta_rho, xi_rho) float32 ...
    ubar        (ocean_time, eta_rho, xi_u) float32 ...
    vbar        (ocean_time, eta_v, xi_rho) float32 ...
    salt        (ocean_time, s_rho, eta_rho, xi_rho) float32 ...
    temp        (ocean_time, s_rho, eta_rho, xi_rho) float32 ...
    lat_rho     (eta_rho, xi_rho) float32 ...
    lon_rho     (eta_rho, xi_rho) float32 ...

Animation utils

In [6]:
from IPython.display import clear_output
from matplotlib import animation, rc
plt.rcParams["animation.html"] = "jshtml"
from mpl_toolkits.axes_grid1 import make_axes_locatable

from gpuocean.utils import PlotHelper
from gpuocean.utils.NetCDFInitialization import depth_integration

def plotSolution(fig, 
                 eta, hu, hv, h, dx, dy, 
                 t, comment = "Oslo",
                 h_min=-0.1, h_max=0.1, 
                 uv_min=-10, uv_max=10,
                 ax=None, sp=None):


    from datetime import timedelta
    fig.suptitle("Time = {:0>8} ({:s})".format(str(timedelta(seconds=int(t))), comment), 
                 fontsize=18,
                 horizontalalignment='left')
    
    ny, nx = eta.shape
    domain_extent = [0, nx*dx, 0, ny*dy]
    
    x_plots = 3
    y_plots = 1
   
    huv_label = ["hu","hv"]

    if (ax is None):
        ax = [None]*x_plots*y_plots
        sp = [None]*x_plots*y_plots

        uv_cmap = plt.cm.coolwarm
        uv_cmap.set_bad("grey", alpha = 1.0)
        
        h_cmap = plt.cm.coolwarm
        h_cmap.set_bad("grey", alpha = 1.0)

        ax[0] = plt.subplot(y_plots, x_plots, 1)
        sp[0] = ax[0].imshow(eta, interpolation="none", origin='lower', 
                             cmap=h_cmap, 
                             vmin=h_min, vmax=h_max, 
                             extent=domain_extent)
        plt.axis('image')
        plt.title("$\zeta{}$")
        divider0 = make_axes_locatable(ax[0])
        cax0 = divider0.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[0],cax=cax0)


        ax[1] = plt.subplot(y_plots, x_plots, 2)
        sp[1] = ax[1].imshow(hu, interpolation="none", origin='lower', 
                            cmap=uv_cmap, 
                            vmin=uv_min, vmax=uv_max, 
                            extent=domain_extent)
        plt.axis('image')
        plt.title("$"+huv_label[0]+"$")
        divider1 = make_axes_locatable(ax[1])
        cax1 = divider1.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[1],cax=cax1)



        ax[2] = plt.subplot(y_plots, x_plots, 3)
        sp[2] = ax[2].imshow(hv, interpolation="none", origin='lower', 
                             cmap=uv_cmap, 
                             vmin=uv_min, vmax=uv_max, 
                             extent=domain_extent)
        plt.axis('image')
        plt.title("$"+huv_label[1]+"$")
        divider2 = make_axes_locatable(ax[2])
        cax2 = divider2.append_axes('right', size='5%', pad=0.05)
        fig.colorbar(sp[2],cax=cax2)

        plt.tight_layout()
            
    else:        
        #Update plots
        fig.sca(ax[0])
        sp[0].set_data(eta)

        fig.sca(ax[1])
        sp[1].set_data(hu)
        
        fig.sca(ax[2])
        sp[2].set_data(hv)
    
    return ax, sp


def ncAnimation(filename, nctype, **kwargs):
    #Create figure and plot initial conditions
    fig = plt.figure(figsize=(20, 6))

    ncfile = Dataset(filename)
    
    if nctype == "ROMS":
        t = ncfile.variables['ocean_time'][:]

        eta = np.ma.array(ncfile["zeta"][:], mask=len(t)*[1-ncfile["mask_rho"][:]])
        u   = np.ma.array(ncfile["ubar"][:], mask=len(t)*[1-ncfile["mask_rho"][:,:-1]])
        v   = np.ma.array(ncfile["vbar"][:], mask=len(t)*[1-ncfile["mask_rho"][:-1,:]])

        H_m = ncfile["h"]

        hu = u*H_m[:,:-1]
        hv = v*H_m[:-1,:]

    elif nctype == "gpuocean":
        t = ncfile["time"][:]

        eta = ncfile["eta"][:]
        hu  = ncfile["hu"][:]
        hv  = ncfile["hv"][:]

        H_m = ncfile["Hm"][:]

    movie_frames = len(t)

    dx = 50
    dy = 50
    
    ax, sp = plotSolution(fig, 
                            eta[0],
                            hu[0],
                            hv[0],
                            H_m,
                            dx, dy, 
                            t[0], 
                            **kwargs)


    #Helper function which simulates and plots the solution    
    def animate(i):
        t_now = t[0] + (i / (movie_frames-1)) * (t[-1] - t[0]) 

        k = np.searchsorted(t, t_now)
        if (k >= eta.shape[0]):
            k = eta.shape[0] - 1
        j = max(0, k-1)
        if (j == k):
            k += 1
        s = (t_now - t[j]) / (t[k] - t[j])

        plotSolution(fig, 
                        ((1-s)*eta[j] + s*eta[k]), 
                        ((1-s)*hu[j]  + s*hu[k]), 
                        ((1-s)*hv[j]  + s*hv[k]), 
                        (H_m+(1-s)*eta[j] + s*eta[k]), 
                        dx, dy, 
                        t_now, 
                        **kwargs, ax=ax, sp=sp)

        clear_output(wait = True)
        #print(progress.getPrintString(i / (movie_frames-1)))

    #Matplotlib for creating an animation
    anim = animation.FuncAnimation(fig, animate, range(movie_frames), interval=250)
    plt.close(fig)
    
    return anim


In [7]:
ncAnimation("/sintef/data/OsloFjord/test.nc", "ROMS")

## Generating GPUOcean Simulation from Input

Initialisation

In [8]:
x0, x1, y0, y1 = 5, 383, 140, 741

In [74]:
from importlib import reload
reload(NetCDFInitialization)

data_args = NetCDFInitialization.getInitialConditions(source_url, x0, x1, y0, y1, norkyst_data=False, download_data=False, land_value=0.0)

Manually removing north identifier!


In [66]:
data_args["dx"], data_args["dy"]

(49.999880249023164, 50.00052016535929)

In [67]:
from gpuocean.SWEsimulators import CDKLM16
sim = CDKLM16.CDKLM16(gpu_ctx, dt=0.0,  **NetCDFInitialization.removeMetadata(data_args), write_netcdf=True)

This will give inaccurate angle along the border!
This will give inaccurate coriolis along the border!


In [68]:
for t in range(1):#range(len(ds.ocean_time)):
    sim.step(3600)

In [ ]:
ncAnimation(sim.sim_writer.output_file_name, "gpuocean")

Check Mixed-Layer Depth

In [ ]:
mld = NetCDFInitialization.MLD(source_url, 1023, min_mld=5, max_mld=40, x0=x0, x1=x1, y0=y0, y1=y1)

In [ ]:
fig, axs = plt.subplots(1,2,figsize=(10,10))

im = axs[0].imshow(mld, cmap="cool", vmin=0.0)
plt.colorbar(im, ax=axs[0], shrink=0.5)

im = axs[1].imshow(np.ma.array(ds.h.data[y0:y1,x0:x1], mask=(ds.h.data[y0:y1,x0:x1]==0)), cmap="cool")
plt.colorbar(im, ax=axs[1], shrink=0.5)

In [ ]:
y_cut = 130

s_pot_densities = NetCDFInitialization.potentialDensities(source_url, t=t, x0=x0, x1=x1, y0=y0, y1=y1)

s_nc = Dataset(source_url)
s_hs   = s_nc["h"][y0:y1,x0:x1]
s_rhos = s_nc["Cs_r"][:]

s_pot_densities_show = np.ma.array(np.zeros((s_pot_densities.shape[1],100)))
for l in range(s_pot_densities.shape[1]):
    d_up = 0 
    for i in reversed(range(len(s_rhos))):
        d = round(-(s_hs[l,y_cut]*s_rhos[i]))
        s_pot_densities_show[l,d_up:d] = s_pot_densities[i][l,y_cut]
        d_up = d
s_pot_densities_show.mask = (s_pot_densities_show==0)

plt.figure(figsize=(15,5))
plt.imshow(s_pot_densities_show.T[0:50], origin="upper", cmap="plasma",  aspect='auto')
plt.colorbar()
plt.scatter(np.arange(s_pot_densities.shape[1]), mld[:,y_cut])